# Import Libraries

In [48]:
import pandas as pd 
import numpy as np
import re
from sklearn.preprocessing import OrdinalEncoder
from sklearn.preprocessing import OneHotEncoder
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_absolute_error as mae


In [2]:
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)

# Load the Data

In [3]:
data = pd.read_csv('train.csv')

# Getting to Know the Data

In [4]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 891 entries, 0 to 890
Data columns (total 12 columns):
 #   Column       Non-Null Count  Dtype  
---  ------       --------------  -----  
 0   PassengerId  891 non-null    int64  
 1   Survived     891 non-null    int64  
 2   Pclass       891 non-null    int64  
 3   Name         891 non-null    object 
 4   Sex          891 non-null    object 
 5   Age          714 non-null    float64
 6   SibSp        891 non-null    int64  
 7   Parch        891 non-null    int64  
 8   Ticket       891 non-null    object 
 9   Fare         891 non-null    float64
 10  Cabin        204 non-null    object 
 11  Embarked     889 non-null    object 
dtypes: float64(2), int64(5), object(5)
memory usage: 83.7+ KB


Notes:

Looks like there is some missing data in the **Age** and **Cabin** and **Embarked**.

In [5]:
data

PassengerId  Survived  Pclass  \
0              1         0       3   
1              2         1       1   
2              3         1       3   
3              4         1       1   
4              5         0       3   
5              6         0       3   
6              7         0       1   
7              8         0       3   
8              9         1       3   
9             10         1       2   
10            11         1       3   
11            12         1       1   
12            13         0       3   
13            14         0       3   
14            15         0       3   
15            16         1       2   
16            17         0       3   
17            18         1       2   
18            19         0       3   
19            20         1       3   
20            21         0       2   
21            22         1       2   
22            23         1       3   
23            24         1       1   
24            25         0       3   
25            26         1       3   
26            27         0       3   
27            28         0       1   
28            29         1       3   
29            30         0       3   
30            31         0       1   
31            32         1       1   
32            33         1       3   
33            34         0       2   
34            35         0       1   
35            36         0       1   
36            37         1       3   
37            38         0       3   
38            39         0       3   
39            40         1       3   
40            41         0       3   
41            42         0       2   
42            43         0       3   
43            44         1       2   
44            45         1       3   
45            46         0       3   
46            47         0       3   
47            48         1       3   
48            49         0       3   
49            50         0       3   
50            51         0       3   
51            52         0       3   
52            53         1       1   
53            54         1       2   
54            55         0       1   
55            56         1       1   
56            57         1       2   
57            58         0       3   
58            59         1       2   
59            60         0       3   
60            61         0       3   
61            62         1       1   
62            63         0       1   
63            64         0       3   
64            65         0       1   
65            66         1       3   
66            67         1       2   
67            68         0       3   
68            69         1       3   
69            70         0       3   
70            71         0       2   
71            72         0       3   
72            73         0       2   
73            74         0       3   
74            75         1       3   
75            76         0       3   
76            77         0       3   
77            78         0       3   
78            79         1       2   
79            80         1       3   
80            81         0       3   
81            82         1       3   
82            83         1       3   
83            84         0       1   
84            85         1       2   
85            86         1       3   
86            87         0       3   
87            88         0       3   
88            89         1       1   
89            90         0       3   
90            91         0       3   
91            92         0       3   
92            93         0       1   
93            94         0       3   
94            95         0       3   
95            96         0       3   
96            97         0       1   
97            98         1       1   
98            99         1       2   
99           100         0       2   
100          101         0       3   
101          102         0       3   
102          103         0       1   
103          104         0       3   
104          10

# Clean the Data

## Dropping the Cabin Column - Only 22% of the cabin numbers were provided.

In [6]:
data = data.drop(['Cabin'], axis=1)

## Removing Passengers that have unkown Embarked Locations.

Note: Only two of the remaining passangers have are missing there Embarked locations.

In [7]:
Embarked_rms = [n for n, x in zip(data.index, data['Embarked'].isnull()) if x is True]

In [8]:
data = data.drop(Embarked_rms, axis=0)

In [9]:
data = data.reset_index()

## Filling in Missing Ages

In [10]:
print(f"There are {data['Age'].isnull().sum()} missing age entries and that is {(data['Age'].isnull().sum()/len(data))*100:0.2f}% of the remaining data.")

There are 177 missing age entries and that is 19.91% of the remaining data.


In [11]:
print(f"The average age is {data['Age'].mean():0.2f} +/- {data['Age'].std():0.2f} years.")

The average age is 29.64 +/- 14.49 years.


## Make New Column of Data Using Titles

In [12]:
titles = []
for n, name, sex, age in zip(data.index, data['Name'], data['Sex'], data['Age']):
    split = re.split('\s+', name)
    for word in split:
        if "." in word and len(word) > 2:
            if word == "Mlle." or word == "Mme.": 
                titles.append("Miss.")
            else:
                titles.append(word) 
            
    if '.' not in name:
        print(name)

Does each person have a title?

In [13]:
print(f"{len(data)} = {len(titles)}")

889 = 889


In [14]:
data['Title'] = titles

In [15]:
data

index  PassengerId  Survived  Pclass  \
0        0            1         0       3   
1        1            2         1       1   
2        2            3         1       3   
3        3            4         1       1   
4        4            5         0       3   
5        5            6         0       3   
6        6            7         0       1   
7        7            8         0       3   
8        8            9         1       3   
9        9           10         1       2   
10      10           11         1       3   
11      11           12         1       1   
12      12           13         0       3   
13      13           14         0       3   
14      14           15         0       3   
15      15           16         1       2   
16      16           17         0       3   
17      17           18         1       2   
18      18           19         0       3   
19      19           20         1       3   
20      20           21         0       2   
21      21           22         1       2   
22      22           23         1       3   
23      23           24         1       1   
24      24           25         0       3   
25      25           26         1       3   
26      26           27         0       3   
27      27           28         0       1   
28      28           29         1       3   
29      29           30         0       3   
30      30           31         0       1   
31      31           32         1       1   
32      32           33         1       3   
33      33           34         0       2   
34      34           35         0       1   
35      35           36         0       1   
36      36           37         1       3   
37      37           38         0       3   
38      38           39         0       3   
39      39           40         1       3   
40      40           41         0       3   
41      41           42         0       2   
42      42           43         0       3   
43      43           44         1       2   
44      44           45         1       3   
45      45           46         0       3   
46      46           47         0       3   
47      47           48         1       3   
48      48           49         0       3   
49      49           50         0       3   
50      50           51         0       3   
51      51           52         0       3   
52      52           53         1       1   
53      53           54         1       2   
54      54           55         0       1   
55      55           56         1       1   
56      56           57         1       2   
57      57           58         0       3   
58      58           59         1       2   
59      59           60         0       3   
60      60           61         0       3   
61      62           63         0       1   
62      63           64         0       3   
63      64           65         0       1   
64      65           66         1       3   
65      66           67         1       2   
66      67           68         0       3   
67      68           69         1       3   
68      69           70         0       3   
69      70           71         0       2   
70      71           72         0       3   
71      72           73         0       2   
72      73           74         0       3   
73      74           75         1       3   
74      75           76         0       3   
75      76           77         0       3   
76      77           78         0       3   
77      78           79         1       2   
78      79           80         1       3   
79      80           81         0       3   
80      81           82         1       3   
81      82           83         1       3   
82      83           84         0       1   
83      84           85         1       2   
84      85           86         1       3   
85      86           87         0       3   
86      87           88         0       3   
87      88           89         1       1   


## Making New Columns by Decomposing Ticket Information

In [16]:
check = "A12"
print(check.isdigit())

False


In [21]:
Ticket_Ex = []
#T1 = 
#T2 = 
#T3 = 
for tick in data['Ticket']:
    if tick.isdigit():
        Ticket_Ex.append(0)
    else: 
        Ticket_Ex.append(1)

In [22]:
data['Ticket_Ex'] = Ticket_Ex

In [23]:
data

index  PassengerId  Survived  Pclass  \
0        0            1         0       3   
1        1            2         1       1   
2        2            3         1       3   
3        3            4         1       1   
4        4            5         0       3   
5        5            6         0       3   
6        6            7         0       1   
7        7            8         0       3   
8        8            9         1       3   
9        9           10         1       2   
10      10           11         1       3   
11      11           12         1       1   
12      12           13         0       3   
13      13           14         0       3   
14      14           15         0       3   
15      15           16         1       2   
16      16           17         0       3   
17      17           18         1       2   
18      18           19         0       3   
19      19           20         1       3   
20      20           21         0       2   
21      21           22         1       2   
22      22           23         1       3   
23      23           24         1       1   
24      24           25         0       3   
25      25           26         1       3   
26      26           27         0       3   
27      27           28         0       1   
28      28           29         1       3   
29      29           30         0       3   
30      30           31         0       1   
31      31           32         1       1   
32      32           33         1       3   
33      33           34         0       2   
34      34           35         0       1   
35      35           36         0       1   
36      36           37         1       3   
37      37           38         0       3   
38      38           39         0       3   
39      39           40         1       3   
40      40           41         0       3   
41      41           42         0       2   
42      42           43         0       3   
43      43           44         1       2   
44      44           45         1       3   
45      45           46         0       3   
46      46           47         0       3   
47      47           48         1       3   
48      48           49         0       3   
49      49           50         0       3   
50      50           51         0       3   
51      51           52         0       3   
52      52           53         1       1   
53      53           54         1       2   
54      54           55         0       1   
55      55           56         1       1   
56      56           57         1       2   
57      57           58         0       3   
58      58           59         1       2   
59      59           60         0       3   
60      60           61         0       3   
61      62           63         0       1   
62      63           64         0       3   
63      64           65         0       1   
64      65           66         1       3   
65      66           67         1       2   
66      67           68         0       3   
67      68           69         1       3   
68      69           70         0       3   
69      70           71         0       2   
70      71           72         0       3   
71      72           73         0       2   
72      73           74         0       3   
73      74           75         1       3   
74      75           76         0       3   
75      76           77         0       3   
76      77           78         0       3   
77      78           79         1       2   
78      79           80         1       3   
79      80           81         0       3   
80      81           82         1       3   
81      82           83         1       3   
82      83           84         0       1   
83      84           85         1       2   
84      85           86         1       3   
85      86           87         0       3   
86      87           88         0       3   
87      88           89         1       1   


## Converting All Categorical Data to Numerical Data

For now I will remove all strings that can not be converted into numerical data such as the names of the passanger (**Name**) and ticket IDs (**Ticket**).

In [24]:
data = data.drop(['Name','Ticket'], axis=1)

In [25]:
data.head()

index  PassengerId  Survived  Pclass     Sex   Age  SibSp  Parch     Fare  \
0      0            1         0       3    male  22.0      1      0   7.2500   
1      1            2         1       1  female  38.0      1      0  71.2833   
2      2            3         1       3  female  26.0      0      0   7.9250   
3      3            4         1       1  female  35.0      1      0  53.1000   
4      4            5         0       3    male  35.0      0      0   8.0500   

  Embarked  Title  Ticket_Ex  
0        S    Mr.          1  
1        C   Mrs.          1  
2        S  Miss.          1  
3        S   Mrs.          0  
4        S    Mr.          0

No I will use the OrdinalEncoder to convert the **Sex** and **Embarked** columns into numerical data.

In [26]:
o_encoder = OrdinalEncoder()
columns_4_o_encoder = ['Sex', 'Embarked']
data[columns_4_o_encoder] = o_encoder.fit_transform(data[columns_4_o_encoder])

In [27]:
data.head()

index  PassengerId  Survived  Pclass  Sex   Age  SibSp  Parch     Fare  \
0      0            1         0       3  1.0  22.0      1      0   7.2500   
1      1            2         1       1  0.0  38.0      1      0  71.2833   
2      2            3         1       3  0.0  26.0      0      0   7.9250   
3      3            4         1       1  0.0  35.0      1      0  53.1000   
4      4            5         0       3  1.0  35.0      0      0   8.0500   

   Embarked  Title  Ticket_Ex  
0       2.0    Mr.          1  
1       0.0   Mrs.          1  
2       2.0  Miss.          1  
3       2.0   Mrs.          0  
4       2.0    Mr.          0

### Use One-hot Enconding on the Passenger Titles.

Since there ~15 different passenger titles (rather low cardinality) they will be treated using One-hot Encoding.

In [28]:
OHE = OneHotEncoder(handle_unknown='ignore', sparse=False)
OHE_df = pd.DataFrame(OHE.fit_transform(data['Title'].to_numpy().reshape(-1,1)))
data = pd.concat([data, OHE_df], axis=1).drop(['Title'], axis=1)

# Current State of the Data

In [29]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 889 entries, 0 to 888
Data columns (total 26 columns):
 #   Column       Non-Null Count  Dtype  
---  ------       --------------  -----  
 0   index        889 non-null    int64  
 1   PassengerId  889 non-null    int64  
 2   Survived     889 non-null    int64  
 3   Pclass       889 non-null    int64  
 4   Sex          889 non-null    float64
 5   Age          712 non-null    float64
 6   SibSp        889 non-null    int64  
 7   Parch        889 non-null    int64  
 8   Fare         889 non-null    float64
 9   Embarked     889 non-null    float64
 10  Ticket_Ex    889 non-null    int64  
 11  0            889 non-null    float64
 12  1            889 non-null    float64
 13  2            889 non-null    float64
 14  3            889 non-null    float64
 15  4            889 non-null    float64
 16  5            889 non-null    float64
 17  6            889 non-null    float64
 18  7            889 non-null    float64
 19  8       

The ages are still missing, but all the rest of the data is filled in. Now I will attempt to calculate the missing ages using a regressor. 

# Setting up and Using Several Machine Learning Methods

## Create a new dataframe that will be used to train and test regressor for prediciting the missing ages.

In [30]:
passengers_w_missing_ages = [n for n, x in zip(data.index, data['Age'].isnull()) if x is True]

The following dataframe is what you will use you trained model on.

In [31]:
passengers_wo_ages_test = data[data.index.isin(passengers_w_missing_ages)]

In [32]:
passengers_wo_ages_test

index  PassengerId  Survived  Pclass  Sex  Age  SibSp  Parch      Fare  \
5        5            6         0       3  1.0  NaN      0      0    8.4583   
17      17           18         1       2  1.0  NaN      0      0   13.0000   
19      19           20         1       3  0.0  NaN      0      0    7.2250   
26      26           27         0       3  1.0  NaN      0      0    7.2250   
28      28           29         1       3  0.0  NaN      0      0    7.8792   
29      29           30         0       3  1.0  NaN      0      0    7.8958   
31      31           32         1       1  0.0  NaN      1      0  146.5208   
32      32           33         1       3  0.0  NaN      0      0    7.7500   
36      36           37         1       3  1.0  NaN      0      0    7.2292   
42      42           43         0       3  1.0  NaN      0      0    7.8958   
45      45           46         0       3  1.0  NaN      0      0    8.0500   
46      46           47         0       3  1.0  NaN      1      0   15.5000   
47      47           48         1       3  0.0  NaN      0      0    7.7500   
48      48           49         0       3  1.0  NaN      2      0   21.6792   
55      55           56         1       1  1.0  NaN      0      0   35.5000   
63      64           65         0       1  1.0  NaN      0      0   27.7208   
64      65           66         1       3  1.0  NaN      1      1   15.2458   
75      76           77         0       3  1.0  NaN      0      0    7.8958   
76      77           78         0       3  1.0  NaN      0      0    8.0500   
81      82           83         1       3  0.0  NaN      0      0    7.7875   
86      87           88         0       3  1.0  NaN      0      0    8.0500   
94      95           96         0       3  1.0  NaN      0      0    8.0500   
100    101          102         0       3  1.0  NaN      0      0    7.8958   
106    107          108         1       3  1.0  NaN      0      0    7.7750   
108    109          110         1       3  0.0  NaN      1      0   24.1500   
120    121          122         0       3  1.0  NaN      0      0    8.0500   
125    126          127         0       3  1.0  NaN      0      0    7.7500   
127    128          129         1       3  0.0  NaN      1      1   22.3583   
139    140          141         0       3  0.0  NaN      0      2   15.2458   
153    154          155         0       3  1.0  NaN      0      0    7.3125   
157    158          159         0       3  1.0  NaN      0      0    8.6625   
158    159          160         0       3  1.0  NaN      8      2   69.5500   
165    166          167         1       1  0.0  NaN      0      1   55.0000   
167    168          169         0       1  1.0  NaN      0      0   25.9250   
175    176          177         0       3  1.0  NaN      3      1   25.4667   
179    180          181         0       3  0.0  NaN      8      2   69.5500   
180    181          182         0       2  1.0  NaN      0      0   15.0500   
184    185          186         0       1  1.0  NaN      0      0   50.0000   
185    186          187         1       3  0.0  NaN      1      0   15.5000   
195    196          197         0       3  1.0  NaN      0      0    7.7500   
197    198          199         1       3  0.0  NaN      0      0    7.7500   
200    201          202         0       3  1.0  NaN      8      2   69.5500   
213    214          215         0       3  1.0  NaN      1      0    7.7500   
222    223          224         0       3  1.0  NaN      0      0    7.8958   
228    229          230         0       3  0.0  NaN      3      1   25.4667   
234    235          236         0       3  0.0  NaN      0      0    7.5500   
239    240          241         0       3  0.0  NaN      1      0   14.4542   
240    241          242         1       3  0.0  NaN      1      0   15.5000   
249    250          251         0       3  1.0  NaN      0      0    7.2500   
255    256          257         1       1  0.0  NaN    

This is the data set that you will use to train your regressor.

In [33]:
passengers_w_ages_train = data.drop(passengers_w_missing_ages, axis=0)

In [34]:
passengers_w_ages_train

index  PassengerId  Survived  Pclass  Sex    Age  SibSp  Parch      Fare  \
0        0            1         0       3  1.0  22.00      1      0    7.2500   
1        1            2         1       1  0.0  38.00      1      0   71.2833   
2        2            3         1       3  0.0  26.00      0      0    7.9250   
3        3            4         1       1  0.0  35.00      1      0   53.1000   
4        4            5         0       3  1.0  35.00      0      0    8.0500   
6        6            7         0       1  1.0  54.00      0      0   51.8625   
7        7            8         0       3  1.0   2.00      3      1   21.0750   
8        8            9         1       3  0.0  27.00      0      2   11.1333   
9        9           10         1       2  0.0  14.00      1      0   30.0708   
10      10           11         1       3  0.0   4.00      1      1   16.7000   
11      11           12         1       1  0.0  58.00      0      0   26.5500   
12      12           13         0       3  1.0  20.00      0      0    8.0500   
13      13           14         0       3  1.0  39.00      1      5   31.2750   
14      14           15         0       3  0.0  14.00      0      0    7.8542   
15      15           16         1       2  0.0  55.00      0      0   16.0000   
16      16           17         0       3  1.0   2.00      4      1   29.1250   
18      18           19         0       3  0.0  31.00      1      0   18.0000   
20      20           21         0       2  1.0  35.00      0      0   26.0000   
21      21           22         1       2  1.0  34.00      0      0   13.0000   
22      22           23         1       3  0.0  15.00      0      0    8.0292   
23      23           24         1       1  1.0  28.00      0      0   35.5000   
24      24           25         0       3  0.0   8.00      3      1   21.0750   
25      25           26         1       3  0.0  38.00      1      5   31.3875   
27      27           28         0       1  1.0  19.00      3      2  263.0000   
30      30           31         0       1  1.0  40.00      0      0   27.7208   
33      33           34         0       2  1.0  66.00      0      0   10.5000   
34      34           35         0       1  1.0  28.00      1      0   82.1708   
35      35           36         0       1  1.0  42.00      1      0   52.0000   
37      37           38         0       3  1.0  21.00      0      0    8.0500   
38      38           39         0       3  0.0  18.00      2      0   18.0000   
39      39           40         1       3  0.0  14.00      1      0   11.2417   
40      40           41         0       3  0.0  40.00      1      0    9.4750   
41      41           42         0       2  0.0  27.00      1      0   21.0000   
43      43           44         1       2  0.0   3.00      1      2   41.5792   
44      44           45         1       3  0.0  19.00      0      0    7.8792   
49      49           50         0       3  0.0  18.00      1      0   17.8000   
50      50           51         0       3  1.0   7.00      4      1   39.6875   
51      51           52         0       3  1.0  21.00      0      0    7.8000   
52      52           53         1       1  0.0  49.00      1      0   76.7292   
53      53           54         1       2  0.0  29.00      1      0   26.0000   
54      54           55         0       1  1.0  65.00      0      1   61.9792   
56      56           57         1       2  0.0  21.00      0      0   10.5000   
57      57           58         0       3  1.0  28.50      0      0    7.2292   
58      58           59         1       2  0.0   5.00      1      2   27.7500   
59      59           60         0       3  1.0  11.00      5      2   46.9000   
60      60           61         0       3  1.0  22.00      0      0    7.2292   
61      62           63         0       1  1.0  45.00      1      0   83.4750   
62      63           64         0       3  1.0   4.00      3      2   27.9000   
65      66           67         1   

## Creating Train and Testing Data to Build and Test the Model

In [35]:
features = [x for x in passengers_w_ages_train.columns if x != 'Age' if x != 'PassengerId']

In [36]:
print(f"Total Number of Features: {len(features)}")

Total Number of Features: 24


In [37]:
x = passengers_w_ages_train[features]
y = passengers_w_ages_train['Age']

In [38]:
x_train, x_valid, y_train, y_valid = train_test_split(x, y, train_size=0.8, test_size=0.2, random_state=42)

## Using the Random Forest Regressor

In [39]:
from sklearn.ensemble import RandomForestRegressor

In [40]:
RF_model = RandomForestRegressor(n_estimators=100, random_state=42)
RF_model.fit(x_train, y_train)
RF_preds = RF_model.predict(x_valid)

In [41]:
print(f"The Mean Absolute Error in the Age Prediction is {mae(y_valid, RF_preds):0.2f} years.")
print(f"The Mean Absolute Error in using the mean age is {mae(y_valid, [data['Age'].mean() for i in range(len(y_valid))]):0.2f} years.")

The Mean Absolute Error in the Age Prediction is 8.85 years.
The Mean Absolute Error in using the mean age is 12.61 years.


In [42]:
from sklearn.ensemble import GradientBoostingRegressor

In [82]:
def booster(xs, ys, zs, x_train, y_train, x_valid, y_valid):
    check = []
    for x in xs:
        for y in ys:
            for z in zs:
                GBR_model = GradientBoostingRegressor(learning_rate=x, n_estimators=z, subsample=y, random_state=42)
                GBR_model.fit(x_train, y_train)
                GBR_preds = GBR_model.predict(x_valid)
                check.append(mae(y_valid, GBR_preds))
                print(mae(y_valid, GBR_preds), x, y, z)
    return(min(check))

In [83]:
xs = list(np.linspace(0.001,0.1, 40))
ys = list(np.linspace(0.01,  1, 20))
zs = [50, 100, 150, 200]

In [84]:
booster(xs, ys, zs, x_train, y_train, x_valid, y_valid)

12.553501805956731 0.001 0.01 50
12.493577206202225 0.001 0.01 100
12.462449902831219 0.001 0.01 150
12.41820064060368 0.001 0.01 200
12.48578672358777 0.001 0.06210526315789474 50
12.35037416725419 0.001 0.06210526315789474 100
12.25513766966424 0.001 0.06210526315789474 150
12.140766942688305 0.001 0.06210526315789474 200
12.444076666976239 0.001 0.11421052631578947 50
12.295427367210468 0.001 0.11421052631578947 100
12.164596017524444 0.001 0.11421052631578947 150
12.037470313774065 0.001 0.11421052631578947 200
12.447174737222515 0.001 0.16631578947368422 50
12.295810563566748 0.001 0.16631578947368422 100
12.137894336834307 0.001 0.16631578947368422 150
11.996784199991026 0.001 0.16631578947368422 200
12.427319120166601 0.001 0.21842105263157896 50
12.256447392858773 0.001 0.21842105263157896 100
12.088180293552849 0.001 0.21842105263157896 150
11.93207410408103 0.001 0.21842105263157896 200
12.405304354095653 0.001 0.2705263157894737 50
12.214804472803339 0.001 0.2705263157894737

10.318912770518464 0.0035384615384615385 0.9478947368421053 200
11.832025935130215 0.0035384615384615385 1.0 50
11.17458199785341 0.0035384615384615385 1.0 100
10.692892733104442 0.0035384615384615385 1.0 150
10.322040140068221 0.0035384615384615385 1.0 200
12.304738072414999 0.006076923076923077 0.01 50
11.99702279039528 0.006076923076923077 0.01 100
11.828854329010792 0.006076923076923077 0.01 150
11.634818855348461 0.006076923076923077 0.01 200
11.917671196100228 0.006076923076923077 0.06210526315789474 50
11.276180357502206 0.006076923076923077 0.06210526315789474 100
10.910899362663248 0.006076923076923077 0.06210526315789474 150
10.642151244795558 0.006076923076923077 0.06210526315789474 200
11.687013533679826 0.006076923076923077 0.11421052631578947 50
11.064176883545679 0.006076923076923077 0.11421052631578947 100
10.611386812905426 0.006076923076923077 0.11421052631578947 150
10.296142010208028 0.006076923076923077 0.11421052631578947 200
11.721866353183119 0.00607692307692307

11.024978697585649 0.008615384615384615 0.6873684210526316 50
10.070755689382295 0.008615384615384615 0.6873684210526316 100
9.53313982376904 0.008615384615384615 0.6873684210526316 150
9.226689762323833 0.008615384615384615 0.6873684210526316 200
11.025278748142167 0.008615384615384615 0.7394736842105263 50
10.069945853760299 0.008615384615384615 0.7394736842105263 100
9.511759465356587 0.008615384615384615 0.7394736842105263 150
9.25051377471201 0.008615384615384615 0.7394736842105263 200
10.99855257546448 0.008615384615384615 0.791578947368421 50
10.077699881308922 0.008615384615384615 0.791578947368421 100
9.515623000827453 0.008615384615384615 0.791578947368421 150
9.239412101410881 0.008615384615384615 0.791578947368421 200
10.996404722638351 0.008615384615384615 0.8436842105263158 50
10.038135848376161 0.008615384615384615 0.8436842105263158 100
9.506290616884177 0.008615384615384615 0.8436842105263158 150
9.191942535081987 0.008615384615384615 0.8436842105263158 200
10.97873547

9.187227243046589 0.013692307692307691 0.37473684210526315 150
8.993807201982468 0.013692307692307691 0.37473684210526315 200
10.464618631429287 0.013692307692307691 0.4268421052631579 50
9.590392769192787 0.013692307692307691 0.4268421052631579 100
9.178081907789597 0.013692307692307691 0.4268421052631579 150
8.950031722740693 0.013692307692307691 0.4268421052631579 200
10.475407555261933 0.013692307692307691 0.4789473684210527 50
9.616952729035138 0.013692307692307691 0.4789473684210527 100
9.213115111132069 0.013692307692307691 0.4789473684210527 150
8.963766764324403 0.013692307692307691 0.4789473684210527 200
10.44748867011139 0.013692307692307691 0.5310526315789474 50
9.553487823087224 0.013692307692307691 0.5310526315789474 100
9.17600990886579 0.013692307692307691 0.5310526315789474 150
8.996786017314111 0.013692307692307691 0.5310526315789474 200
10.402652875515782 0.013692307692307691 0.5831578947368421 50
9.44194273966602 0.013692307692307691 0.5831578947368421 100
9.0971832

9.417796482733918 0.01876923076923077 0.06210526315789474 200
10.481525908063505 0.01876923076923077 0.11421052631578947 50
9.586647190665005 0.01876923076923077 0.11421052631578947 100
9.322335811327056 0.01876923076923077 0.11421052631578947 150
9.110133941710686 0.01876923076923077 0.11421052631578947 200
10.57354440356358 0.01876923076923077 0.16631578947368422 50
9.744130092472842 0.01876923076923077 0.16631578947368422 100
9.371151017568788 0.01876923076923077 0.16631578947368422 150
9.217870978250366 0.01876923076923077 0.16631578947368422 200
10.316057037340078 0.01876923076923077 0.21842105263157896 50
9.507900703711412 0.01876923076923077 0.21842105263157896 100
9.225941609760866 0.01876923076923077 0.21842105263157896 150
9.069291245683738 0.01876923076923077 0.21842105263157896 200
10.183405706039727 0.01876923076923077 0.2705263157894737 50
9.427138725311677 0.01876923076923077 0.2705263157894737 100
9.070910422240562 0.01876923076923077 0.2705263157894737 150
8.9116495364

...

8.491246257812476 0.08476923076923078 0.8436842105263158 200
8.629882552628457 0.08476923076923078 0.8957894736842106 50
8.506562511234847 0.08476923076923078 0.8957894736842106 100
8.467959291768432 0.08476923076923078 0.8957894736842106 150
8.604415744901067 0.08476923076923078 0.8957894736842106 200
8.456460254850812 0.08476923076923078 0.9478947368421053 50
8.47967956001719 0.08476923076923078 0.9478947368421053 100
8.547209222594915 0.08476923076923078 0.9478947368421053 150
8.623374698119981 0.08476923076923078 0.9478947368421053 200
8.615382768573328 0.08476923076923078 1.0 50
8.45591595319072 0.08476923076923078 1.0 100
8.479090008515318 0.08476923076923078 1.0 150
8.641792081324747 0.08476923076923078 1.0 200
11.044320964140926 0.08730769230769231 0.01 50
10.38849286349546 0.08730769230769231 0.01 100
10.233192985798862 0.08730769230769231 0.01 150
10.896397518795272 0.08730769230769231 0.01 200
9.802082827593196 0.08730769230769231 0.06210526315789474 50
9.348020137887103 0.0

8.68562914355604 0.08984615384615385 0.6352631578947369 50
8.484377128557114 0.08984615384615385 0.6352631578947369 100
8.571555012045664 0.08984615384615385 0.6352631578947369 150
8.567840673528405 0.08984615384615385 0.6352631578947369 200
8.701711813247142 0.08984615384615385 0.6873684210526316 50
8.614502273423218 0.08984615384615385 0.6873684210526316 100
8.66357491359992 0.08984615384615385 0.6873684210526316 150
8.760943891279968 0.08984615384615385 0.6873684210526316 200
8.558589761278844 0.08984615384615385 0.7394736842105263 50
8.520444728429862 0.08984615384615385 0.7394736842105263 100
8.612791700266438 0.08984615384615385 0.7394736842105263 150
8.602079082561632 0.08984615384615385 0.7394736842105263 200
8.614522342729273 0.08984615384615385 0.791578947368421 50
8.580386939039567 0.08984615384615385 0.791578947368421 100
8.675388828427417 0.08984615384615385 0.791578947368421 150
8.669440189511562 0.08984615384615385 0.791578947368421 200
8.73372161065338 0.089846153846153

8.765177815448315 0.09492307692307693 0.37473684210526315 200
8.596759401022615 0.09492307692307693 0.4268421052631579 50
8.53463125356481 0.09492307692307693 0.4268421052631579 100
8.688590089816818 0.09492307692307693 0.4268421052631579 150
8.857156848244095 0.09492307692307693 0.4268421052631579 200
8.623756732920508 0.09492307692307693 0.4789473684210527 50
8.772414551146857 0.09492307692307693 0.4789473684210527 100
8.864968414203963 0.09492307692307693 0.4789473684210527 150
8.889394585494607 0.09492307692307693 0.4789473684210527 200
8.79517739059284 0.09492307692307693 0.5310526315789474 50
8.580461314918221 0.09492307692307693 0.5310526315789474 100
8.431517496067881 0.09492307692307693 0.5310526315789474 150
8.527561340760894 0.09492307692307693 0.5310526315789474 200
8.610069237715715 0.09492307692307693 0.5831578947368421 50
8.538117630168703 0.09492307692307693 0.5831578947368421 100
8.496642915309286 0.09492307692307693 0.5831578947368421 150
8.590648579539584 0.094923076

8.991025992340814 0.1 0.16631578947368422 150
8.918457087583327 0.1 0.16631578947368422 200
8.650966167935364 0.1 0.21842105263157896 50
8.513771421709416 0.1 0.21842105263157896 100
8.88125307179861 0.1 0.21842105263157896 150
9.020998597484203 0.1 0.21842105263157896 200
8.989410516042758 0.1 0.2705263157894737 50
8.64511548390999 0.1 0.2705263157894737 100
8.797433976738766 0.1 0.2705263157894737 150
9.008780113516293 0.1 0.2705263157894737 200
8.696696755378097 0.1 0.32263157894736844 50
8.800808661601652 0.1 0.32263157894736844 100
9.01232461957106 0.1 0.32263157894736844 150
9.201136431989944 0.1 0.32263157894736844 200
8.49024126324251 0.1 0.37473684210526315 50
8.322933068074642 0.1 0.37473684210526315 100
8.580296255417762 0.1 0.37473684210526315 150
8.670300634276183 0.1 0.37473684210526315 200
8.594157562537024 0.1 0.4268421052631579 50
8.610279011929329 0.1 0.4268421052631579 100
8.58571205339382 0.1 0.4268421052631579 150
8.82206752258527 0.1 0.4268421052631579 200
8.68240

8.288999750809802

In [87]:
GBR_model = GradientBoostingRegressor(learning_rate=0.08223076923076923, n_estimators=150, subsample=0.4268421052631579, random_state=42)
GBR_model.fit(x_train, y_train)
GBR_preds = GBR_model.predict(x_valid)

In [88]:
print(f"The Mean Absolute Error in the Age Prediction is {mae(y_valid, GBR_preds):0.2f} years.")
print(f"The Mean Absolute Error in using the mean age is {mae(y_valid, [data['Age'].mean() for i in range(len(y_valid))]):0.2f} years.")

The Mean Absolute Error in the Age Prediction is 8.29 years.
The Mean Absolute Error in using the mean age is 12.61 years.


# Conclusion 

In conclusion there is a slight increase in the age prediction compared to using a standard mean value for all missing ages and should be added back into the main dataset. 

# Finally Prediction of the Missing Ages

Using the best model from above generate predictions of the missing ages. 

In [89]:
final_x = passengers_wo_ages_test[features]

In [90]:
final_ages = GBR_model.predict(final_x)

In [91]:
final_ages

array([34.40928611, 36.53011749, 32.87838269, 28.426806  , 23.96020775,
       35.40278562, 32.1698923 , 33.97374283, 22.2799067 , 24.05280737,
       26.44249426, 28.68676644, 23.04746895, 22.23175344, 43.13678949,
       45.40572015,  4.3718939 , 27.81338077, 30.09612662, 20.98844269,
       29.46970526, 30.32662408, 28.69482114, 26.3544944 , 18.03127099,
       29.60062186, 34.62610051,  7.04082209, 24.47313947, 31.40981822,
       34.40384854,  9.20587019, 36.47224212, 47.37986555,  6.56745677,
       10.49968726, 31.95869194, 48.18497636, 27.57594841, 35.52564659,
       26.83748171, 19.13988339, 31.82855583, 28.55803169,  9.46501548,
       24.57818532, 19.96064027, 18.84227865, 30.08828417, 41.08131694,
       38.14823126, 31.82799924, 48.03248137, 29.6532407 , 33.62821669,
       48.53536579, 43.58125776, 38.88248596, 26.21363427, 23.03051333,
       25.32174692, 30.82509898, 30.64242392, 19.98178511, 15.19545631,
       34.28703317, 29.091462  , 27.21750108, 49.02779975, 27.50

# Replace Data

In [92]:
missing_ages_filled = passengers_wo_ages_test.drop(['Age'], axis=1)

In [93]:
missing_ages_filled['Age'] = final_ages

In [94]:
missing_ages_filled = missing_ages_filled[passengers_w_ages_train.columns.to_list()] 

In [95]:
missing_ages_filled

index  PassengerId  Survived  Pclass  Sex        Age  SibSp  Parch  \
5        5            6         0       3  1.0  34.409286      0      0   
17      17           18         1       2  1.0  36.530117      0      0   
19      19           20         1       3  0.0  32.878383      0      0   
26      26           27         0       3  1.0  28.426806      0      0   
28      28           29         1       3  0.0  23.960208      0      0   
29      29           30         0       3  1.0  35.402786      0      0   
31      31           32         1       1  0.0  32.169892      1      0   
32      32           33         1       3  0.0  33.973743      0      0   
36      36           37         1       3  1.0  22.279907      0      0   
42      42           43         0       3  1.0  24.052807      0      0   
45      45           46         0       3  1.0  26.442494      0      0   
46      46           47         0       3  1.0  28.686766      1      0   
47      47           48         1       3  0.0  23.047469      0      0   
48      48           49         0       3  1.0  22.231753      2      0   
55      55           56         1       1  1.0  43.136789      0      0   
63      64           65         0       1  1.0  45.405720      0      0   
64      65           66         1       3  1.0   4.371894      1      1   
75      76           77         0       3  1.0  27.813381      0      0   
76      77           78         0       3  1.0  30.096127      0      0   
81      82           83         1       3  0.0  20.988443      0      0   
86      87           88         0       3  1.0  29.469705      0      0   
94      95           96         0       3  1.0  30.326624      0      0   
100    101          102         0       3  1.0  28.694821      0      0   
106    107          108         1       3  1.0  26.354494      0      0   
108    109          110         1       3  0.0  18.031271      1      0   
120    121          122         0       3  1.0  29.600622      0      0   
125    126          127         0       3  1.0  34.626101      0      0   
127    128          129         1       3  0.0   7.040822      1      1   
139    140          141         0       3  0.0  24.473139      0      2   
153    154          155         0       3  1.0  31.409818      0      0   
157    158          159         0       3  1.0  34.403849      0      0   
158    159          160         0       3  1.0   9.205870      8      2   
165    166          167         1       1  0.0  36.472242      0      1   
167    168          169         0       1  1.0  47.379866      0      0   
175    176          177         0       3  1.0   6.567457      3      1   
179    180          181         0       3  0.0  10.499687      8      2   
180    181          182         0       2  1.0  31.958692      0      0   
184    185          186         0       1  1.0  48.184976      0      0   
185    186          187         1       3  0.0  27.575948      1      0   
195    196          197         0       3  1.0  35.525647      0      0   
197    198          199         1       3  0.0  26.837482      0      0   
200    201          202         0       3  1.0  19.139883      8      2   
213    214          215         0       3  1.0  31.828556      1      0   
222    223          224         0       3  1.0  28.558032      0      0   
228    229          230         0       3  0.0   9.465015      3      1   
234    235          236         0       3  0.0  24.578185      0      0   
239    240          241         0       3  0.0  19.960640      1      0   
240    241          242         1       3  0.0  18.842279      1      0   
249    250          251         0       3  1.0  30.088284      0      0   
255    256          257         1       1  0.0  41.081317      0      0   
259    260          261         0       3  1.0  38.148231      0      0   
263    264          265         0       3  0.0  31.827999      0      0   
269    270          271       

In [96]:
final_data = pd.concat([passengers_w_ages_train, missing_ages_filled], axis=0).drop(['index'], axis=1)
final_data.sort_values(['PassengerId'], inplace=True)

In [97]:
final_data

PassengerId  Survived  Pclass  Sex        Age  SibSp  Parch      Fare  \
0              1         0       3  1.0  22.000000      1      0    7.2500   
1              2         1       1  0.0  38.000000      1      0   71.2833   
2              3         1       3  0.0  26.000000      0      0    7.9250   
3              4         1       1  0.0  35.000000      1      0   53.1000   
4              5         0       3  1.0  35.000000      0      0    8.0500   
5              6         0       3  1.0  34.409286      0      0    8.4583   
6              7         0       1  1.0  54.000000      0      0   51.8625   
7              8         0       3  1.0   2.000000      3      1   21.0750   
8              9         1       3  0.0  27.000000      0      2   11.1333   
9             10         1       2  0.0  14.000000      1      0   30.0708   
10            11         1       3  0.0   4.000000      1      1   16.7000   
11            12         1       1  0.0  58.000000      0      0   26.5500   
12            13         0       3  1.0  20.000000      0      0    8.0500   
13            14         0       3  1.0  39.000000      1      5   31.2750   
14            15         0       3  0.0  14.000000      0      0    7.8542   
15            16         1       2  0.0  55.000000      0      0   16.0000   
16            17         0       3  1.0   2.000000      4      1   29.1250   
17            18         1       2  1.0  36.530117      0      0   13.0000   
18            19         0       3  0.0  31.000000      1      0   18.0000   
19            20         1       3  0.0  32.878383      0      0    7.2250   
20            21         0       2  1.0  35.000000      0      0   26.0000   
21            22         1       2  1.0  34.000000      0      0   13.0000   
22            23         1       3  0.0  15.000000      0      0    8.0292   
23            24         1       1  1.0  28.000000      0      0   35.5000   
24            25         0       3  0.0   8.000000      3      1   21.0750   
25            26         1       3  0.0  38.000000      1      5   31.3875   
26            27         0       3  1.0  28.426806      0      0    7.2250   
27            28         0       1  1.0  19.000000      3      2  263.0000   
28            29         1       3  0.0  23.960208      0      0    7.8792   
29            30         0       3  1.0  35.402786      0      0    7.8958   
30            31         0       1  1.0  40.000000      0      0   27.7208   
31            32         1       1  0.0  32.169892      1      0  146.5208   
32            33         1       3  0.0  33.973743      0      0    7.7500   
33            34         0       2  1.0  66.000000      0      0   10.5000   
34            35         0       1  1.0  28.000000      1      0   82.1708   
35            36         0       1  1.0  42.000000      1      0   52.0000   
36            37         1       3  1.0  22.279907      0      0    7.2292   
37            38         0       3  1.0  21.000000      0      0    8.0500   
38            39         0       3  0.0  18.000000      2      0   18.0000   
39            40         1       3  0.0  14.000000      1      0   11.2417   
40            41         0       3  0.0  40.000000      1      0    9.4750   
41            42         0       2  0.0  27.000000      1      0   21.0000   
42            43         0       3  1.0  24.052807      0      0    7.8958   
43            44         1       2  0.0   3.000000      1      2   41.5792   
44            45         1       3  0.0  19.000000      0      0    7.8792   
45            46         0       3  1.0  26.442494      0      0    8.0500   
46            47         0       3  1.0  28.686766      1      0   15.5000   
47            48         1       3  0.0  23.047469      0      0    7.7500   
48            49         0       3  1.0  22.231753      2      0   21.6792   
49            50         0       3  0.0  18.000000      1      0   17.8000   
50            51         0 

In [98]:
final_data.to_csv('new_data_v2.csv', index=False) 